In [8]:
import pandas as pd
import numpy as np
import json

from pprint import pprint

from sklearn.preprocessing import StandardScaler, OneHotEncoder

pd.set_option('display.max_columns', 500)
pd.set_option('display.max_rows', 500)

In [9]:
with open('./rsc/fxn_grps.json', 'r') as fp:
    fxn_grp_dict = json.load(fp)
    
with open('./rsc/df_columns.json', 'r') as fp:
    column_filters = json.load(fp)
    
compounds = list(fxn_grp_dict.keys())

In [11]:
raw_df = pd.read_csv('./data/bfo_df_20211206.csv')
raw_df = raw_df.dropna(thresh=1)
print('Number of recipes: ', len(raw_df))
print('Number of papers: ', raw_df['doi'].nunique())

df = raw_df.loc[:, column_filters['master']]
display(df)

df.to_csv('./data/bfo_df_master_20211206.csv')

Number of recipes:  357
Number of papers:  179


recipe_id                                                url  \
0          1.0  https://link.springer.com/content/pdf/10.1007/...   
1          2.0  https://link.springer.com/article/10.1007/s108...   
2          3.0  https://www.researchgate.net/profile/Muniyandi...   
3          4.0                                                NaN   
4          5.0                                                NaN   
5          6.0                                                NaN   
6          7.0                                                NaN   
7          8.0  https://link.springer.com/article/10.1007/s108...   
8          9.0  https://link.springer.com/article/10.1007/s108...   
9         10.0  https://link.springer.com/article/10.1007/s108...   
10        11.0                                                NaN   
11        12.0                                                NaN   
12        13.0  https://www.proquest.com/docview/1711184059/fu...   
13        14.0  https://link.springer.com/article/10.1007/s108...   
14        15.0                                                NaN   
15        16.0  https://link.springer.com/article/10.1007/s108...   
16        17.0                                                NaN   
17        18.0                                                NaN   
18        19.0                                                NaN   
19        20.0                                                NaN   
20        21.0  https://link.springer.com/article/10.1007/s108...   
21        22.0  https://link.springer.com/content/pdf/10.1007/...   
22        23.0  https://link.springer.com/article/10.1007/s108...   
23        24.0  https://link.springer.com/article/10.1007/s108...   
24        25.0  https://link.springer.com/article/10.1007/s109...   
25        26.0  https://link.springer.com/article/10.1007/s109...   
26        27.0  https://www.sciencedirect.com/science/article/...   
27        28.0  https://www.sciencedirect.com/science/article/...   
28        29.0  https://www.sciencedirect.com/science/article/...   
29        30.0  https://www.sciencedirect.com/science/article/...   
30        31.0  https://www.sciencedirect.com/science/article/...   
31        32.0  https://www.sciencedirect.com/science/article/...   
32        33.0  https://www.sciencedirect.com/science/article/...   
33        34.0  https://www.sciencedirect.com/science/article/...   
34        35.0                                                NaN   
35        36.0                                                NaN   
36        37.0                                                NaN   
37        38.0  https://www.sciencedirect.com/science/article/...   
38        39.0                                                NaN   
39        40.0                                                NaN   
40        41.0                                                NaN   
41        42.0                                                NaN   
42        43.0                                                NaN   
43        44.0                                                NaN   
44        45.0                                                NaN   
45        46.0                                                NaN   
46        47.0                                                NaN   
47        48.0                                                NaN   
48        49.0                                                NaN   
49        50.0  https://www.sciencedirect.com/science/article/...   
50        51.0  https://www.sciencedirect.com/science/article/...   
51        52.0  https://pubs.rsc.org/en/content/articlehtml/20...   
52        53.0  https://pubs.rsc.org/en/content/articlehtml/20...   
53        54.0  https://aip.scitation.org/doi/full/10.1063/1.2...   
54        55.0                                                NaN   
55        56.0                                                NaN   
56        57.0                                                NaN   
57 

In [4]:
#codify impurity presence
impurity_codes = []
for cmp in df['reported_impurities'].tolist():
    if cmp == '[]':
        impurity_codes.append(0)
    else:
        impurity_codes.append(1)
        
df['impurity_code'] = impurity_codes

In [5]:
#codify Bi/Fe precursor
nitrate_precs = []
for i, (bi, fe) in enumerate(
    zip(df['source_Bi'].to_list(), 
        df['source_Fe'].to_list())
):
    if bi == 'bi_nitrate_pentahydrate' and fe == 'fe_nitrate_nonahydrate':
        nitrate_precs.append(1)
    elif bi == 'bi_nitrate_pentahydrate' or fe == 'fe_nitrate_nonahydrate':
        nitrate_precs.append(0) #Fe is always the other, never Bi
    else:
        nitrate_precs.append(-1)
        
df['nitrate_precs'] = nitrate_precs

In [6]:
df['separate_hydrolysis'].fillna(False, inplace=True)
df['separate_hydrolysis'] = df['separate_hydrolysis'].astype(int)

In [7]:
df.replace({'acetic_acid_glacial' : 'acetic_anhydride'}, inplace=True)
display(df)

recipe_id                                                url  \
0          1.0  https://link.springer.com/content/pdf/10.1007/...   
1          2.0  https://link.springer.com/article/10.1007/s108...   
2          3.0  https://www.researchgate.net/profile/Muniyandi...   
3          4.0                                                NaN   
4          5.0                                                NaN   
5          6.0                                                NaN   
6          7.0                                                NaN   
7          8.0  https://link.springer.com/article/10.1007/s108...   
8          9.0  https://link.springer.com/article/10.1007/s108...   
9         10.0  https://link.springer.com/article/10.1007/s108...   
10        11.0                                                NaN   
11        12.0                                                NaN   
12        13.0  https://www.proquest.com/docview/1711184059/fu...   
13        14.0  https://link.springer.com/article/10.1007/s108...   
14        15.0                                                NaN   
15        16.0  https://link.springer.com/article/10.1007/s108...   
16        17.0                                                NaN   
17        18.0                                                NaN   
18        19.0                                                NaN   
19        20.0                                                NaN   
20        21.0  https://link.springer.com/article/10.1007/s108...   
21        22.0  https://link.springer.com/content/pdf/10.1007/...   
22        23.0  https://link.springer.com/article/10.1007/s108...   
23        24.0  https://link.springer.com/article/10.1007/s108...   
24        25.0  https://link.springer.com/article/10.1007/s109...   
25        26.0  https://link.springer.com/article/10.1007/s109...   
26        27.0  https://www.sciencedirect.com/science/article/...   
27        28.0  https://www.sciencedirect.com/science/article/...   
28        29.0  https://www.sciencedirect.com/science/article/...   
29        30.0  https://www.sciencedirect.com/science/article/...   
30        31.0  https://www.sciencedirect.com/science/article/...   
31        32.0  https://www.sciencedirect.com/science/article/...   
32        33.0  https://www.sciencedirect.com/science/article/...   
33        34.0  https://www.sciencedirect.com/science/article/...   
34        35.0                                                NaN   
35        36.0                                                NaN   
36        37.0                                                NaN   
37        38.0  https://www.sciencedirect.com/science/article/...   
38        39.0                                                NaN   
39        40.0                                                NaN   
40        41.0                                                NaN   
41        42.0                                                NaN   
42        43.0                                                NaN   
43        44.0                                                NaN   
44        45.0                                                NaN   
45        46.0                                                NaN   
46        47.0                                                NaN   
47        48.0                                                NaN   
48        49.0                                                NaN   
49        50.0  https://www.sciencedirect.com/science/article/...   
50        51.0  https://www.sciencedirect.com/science/article/...   
51        52.0  https://pubs.rsc.org/en/content/articlehtml/20...   
52        53.0  https://pubs.rsc.org/en/content/articlehtml/20...   
53        54.0  https://aip.scitation.org/doi/full/10.1063/1.2...   
54        55.0                                                NaN   
55        56.0                                                NaN   
56        57.0                                                NaN   
57 

In [8]:
ohe = OneHotEncoder()
def get_ohes(df, column):
    ohe.fit(df[[column]])
    return pd.DataFrame(
        ohe.transform(df[[column]]).todense(),
        columns=ohe.get_feature_names([column]),
        index=df.index
    )

In [9]:
solvents = [
    '2_methoxyethanol',
    'ethylene_glycol'
]

chelating_agents = [
    'acetic_acid',
    'citric_acid'
]

dehydrating_agents = [
    'acetic_anhydride',
    'acetylacetone'
]

ohe_dfs = {
    'ohe_solvent1' : get_ohes(df, 'solvent1'),
    'ohe_solvent2' : get_ohes(df, 'solvent2'),
    'ohe_chelating_agent1' : get_ohes(df, 'chelating_agent1'),
    'ohe_chelating_agent2' : get_ohes(df, 'chelating_agent2'),
    'ohe_chelating_agent3' : get_ohes(df, 'chelating_agent3'),
    'ohe_dehydrating_agent1' : get_ohes(df, 'dehydrating_agent1'),
    'ohe_dehydrating_agent2' : get_ohes(df, 'dehydrating_agent2'),
    'ohe_surfactant' : get_ohes(df, 'surfactant') 
}

for frame in ohe_dfs.keys():
    df = pd.concat((df, ohe_dfs[frame]), axis=1)
    
for solv in solvents:
    columns = [col for col in df.columns if "_" + solv in col]
    df[solv] = df[columns].sum(axis=1)  
    df[solv].clip(upper=1.0, inplace=True)
    df = df.drop(columns, axis=1)
    
for chel in chelating_agents:
    columns = [col for col in df.columns if "_" + chel in col]
    df[chel] = df[columns].sum(axis=1)  
    df = df.drop(columns, axis=1)

for dehy in dehydrating_agents:
    columns = [col for col in df.columns if "_" + dehy in col]
    df[dehy] = df[columns].sum(axis=1)  
    df = df.drop(columns, axis=1)

display(df)

recipe_id                                                url  \
0          1.0  https://link.springer.com/content/pdf/10.1007/...   
1          2.0  https://link.springer.com/article/10.1007/s108...   
2          3.0  https://www.researchgate.net/profile/Muniyandi...   
3          4.0                                                NaN   
4          5.0                                                NaN   
5          6.0                                                NaN   
6          7.0                                                NaN   
7          8.0  https://link.springer.com/article/10.1007/s108...   
8          9.0  https://link.springer.com/article/10.1007/s108...   
9         10.0  https://link.springer.com/article/10.1007/s108...   
10        11.0                                                NaN   
11        12.0                                                NaN   
12        13.0  https://www.proquest.com/docview/1711184059/fu...   
13        14.0  https://link.springer.com/article/10.1007/s108...   
14        15.0                                                NaN   
15        16.0  https://link.springer.com/article/10.1007/s108...   
16        17.0                                                NaN   
17        18.0                                                NaN   
18        19.0                                                NaN   
19        20.0                                                NaN   
20        21.0  https://link.springer.com/article/10.1007/s108...   
21        22.0  https://link.springer.com/content/pdf/10.1007/...   
22        23.0  https://link.springer.com/article/10.1007/s108...   
23        24.0  https://link.springer.com/article/10.1007/s108...   
24        25.0  https://link.springer.com/article/10.1007/s109...   
25        26.0  https://link.springer.com/article/10.1007/s109...   
26        27.0  https://www.sciencedirect.com/science/article/...   
27        28.0  https://www.sciencedirect.com/science/article/...   
28        29.0  https://www.sciencedirect.com/science/article/...   
29        30.0  https://www.sciencedirect.com/science/article/...   
30        31.0  https://www.sciencedirect.com/science/article/...   
31        32.0  https://www.sciencedirect.com/science/article/...   
32        33.0  https://www.sciencedirect.com/science/article/...   
33        34.0  https://www.sciencedirect.com/science/article/...   
34        35.0                                                NaN   
35        36.0                                                NaN   
36        37.0                                                NaN   
37        38.0  https://www.sciencedirect.com/science/article/...   
38        39.0                                                NaN   
39        40.0                                                NaN   
40        41.0                                                NaN   
41        42.0                                                NaN   
42        43.0                                                NaN   
43        44.0                                                NaN   
44        45.0                                                NaN   
45        46.0                                                NaN   
46        47.0                                                NaN   
47        48.0                                                NaN   
48        49.0                                                NaN   
49        50.0  https://www.sciencedirect.com/science/article/...   
50        51.0  https://www.sciencedirect.com/science/article/...   
51        52.0  https://pubs.rsc.org/en/content/articlehtml/20...   
52        53.0  https://pubs.rsc.org/en/content/articlehtml/20...   
53        54.0  https://aip.scitation.org/doi/full/10.1063/1.2...   
54        55.0                                                NaN   
55        56.0                                                NaN   
56        57.0                                                NaN   
57 

In [10]:
#codify atmosphere
air_atm = []
o2_atm = []
n2_atm = []
for atm in df['atmosphere'].tolist():
    if atm == 'O2':
        air_atm.append(0)
        o2_atm.append(1)
        n2_atm.append(0)
    elif atm == 'N2':
        air_atm.append(0)
        o2_atm.append(0)
        n2_atm.append(1)
    else:
        air_atm.append(1)
        o2_atm.append(0)
        n2_atm.append(0)
        
df['air_atm'] = air_atm
df['o2_atm'] = o2_atm
df['n2_atm'] = n2_atm

In [11]:
#assume blank prebake temps are 0
df['layer_prebake_degC'] = df['layer_prebake_degC'].fillna(0)
df['final_prebake_degC'] = df['final_prebake_degC'].fillna(0)

#assume blank prebake times with no temp are zero
df['layer_prebake_time_min'] = df[['layer_prebake_time_min', 'layer_prebake_degC']].apply(
    lambda rec: 0 if rec['layer_prebake_degC']==0 else rec['layer_prebake_time_min'],
    axis=1
)

df['final_prebake_time_min'] = df[['final_prebake_time_min', 'final_prebake_degC']].apply(
    lambda rec: 0 if rec['final_prebake_degC']==0 else rec['final_prebake_time_min'],
    axis=1
)

df['final_prebake_time_min'] = df[['layer_prebake_time_min', 'final_prebake_time_min']].apply(
    lambda rec: rec['layer_prebake_time_min'] if rec['final_prebake_time_min']==0 else rec['final_prebake_time_min'],
    axis=1
)
df['final_prebake_degC'] = df[['layer_prebake_degC', 'final_prebake_degC']].apply(
    lambda rec: rec['layer_prebake_degC'] if rec['final_prebake_degC']==0 else rec['final_prebake_degC'],
    axis=1
)

# WARNING: NEED TO EDIT THIS (among many other things)
df['final_prebake_time_min'] = df['final_prebake_time_min'].fillna(df['final_prebake_time_min'].median())

display(df['final_prebake_degC'])

0      280.0
1        0.0
2        0.0
3      350.0
4      350.0
5      350.0
6      350.0
7      200.0
8      350.0
9      300.0
10     300.0
11     300.0
12     200.0
13       0.0
14       0.0
15     350.0
16     350.0
17     350.0
18     350.0
19     350.0
20     300.0
21     350.0
22     350.0
23       0.0
24       0.0
25     200.0
26       0.0
27       0.0
28     250.0
29     350.0
30       0.0
31     350.0
32       0.0
33     250.0
34     250.0
35     250.0
36     250.0
37     380.0
38     380.0
39     380.0
40     380.0
41     380.0
42     380.0
43     380.0
44     380.0
45     380.0
46     380.0
47     380.0
48     380.0
49     235.0
50       0.0
51       0.0
52     350.0
53     350.0
54     350.0
55     350.0
56     350.0
57       0.0
58     260.0
59     300.0
60     300.0
61     300.0
62     300.0
63     300.0
64     300.0
65     200.0
66     300.0
67       0.0
68       0.0
69       0.0
70       0.0
71     250.0
72     240.0
73     350.0
74     350.0
75     380.0
76     200.0

In [12]:
df['final_annealing_degC'] = df['final_annealing_degC'].fillna(0)

df['final_annealing_degC'] = df[['layer_annealing_degC', 'final_annealing_degC']].apply(
    lambda rec: rec['layer_annealing_degC'] if rec['final_annealing_degC'] == 0 else rec['final_annealing_degC'],
    axis=1
)
df['final_annealing_degC'] = df['final_annealing_degC'].fillna(0)

df['layer_annealing_degC'] = df['layer_annealing_degC'].fillna(0)
df['layer_annealing_time_min'] = df['layer_annealing_time_min'].fillna(0)

display(df['final_annealing_degC'])

0      550.0
1      550.0
2      600.0
3      600.0
4      500.0
5      500.0
6      500.0
7      300.0
8      500.0
9      600.0
10     550.0
11     500.0
12     300.0
13     600.0
14     550.0
15     525.0
16     525.0
17     525.0
18     525.0
19     525.0
20     500.0
21     550.0
22     500.0
23     285.0
24     500.0
25     550.0
26     500.0
27     300.0
28     600.0
29     600.0
30     550.0
31     500.0
32     500.0
33     500.0
34     450.0
35     400.0
36     300.0
37     500.0
38     500.0
39     500.0
40     500.0
41     550.0
42     550.0
43     550.0
44     550.0
45     550.0
46     550.0
47     550.0
48     550.0
49     550.0
50     550.0
51     500.0
52     600.0
53     450.0
54     500.0
55     550.0
56     600.0
57     550.0
58     300.0
59     550.0
60     550.0
61     550.0
62     550.0
63     550.0
64     550.0
65     550.0
66     600.0
67     600.0
68     600.0
69     550.0
70     550.0
71     600.0
72     550.0
73     550.0
74     550.0
75     550.0
76     550.0

In [13]:
df['final_annealing_time_hr'] = df['final_annealing_time_hr'].fillna(0)

df['final_annealing_time_hr'] = df[['layer_annealing_time_min', 'final_annealing_time_hr']].apply(
    lambda rec: rec['layer_annealing_time_min'] if rec['final_annealing_time_hr'] == 0 else rec['final_annealing_time_hr'],
    axis=1
)
df['final_annealing_time_hr'] = df['final_annealing_time_hr'].fillna(0)

display(df['final_annealing_time_hr'])

0        0.333333
1        0.750000
2        1.000000
3        1.000000
4        3.000000
5        6.000000
6        9.000000
7        0.333333
8        9.000000
9        1.000000
10       1.000000
11       1.000000
12       0.333333
13      15.000000
14      15.000000
15       5.000000
16       5.000000
17       5.000000
18       5.000000
19       5.000000
20     120.000000
21      30.000000
22       1.000000
23       0.333333
24       0.000000
25       0.500000
26       1.000000
27       0.333333
28       0.166667
29       1.000000
30       0.083333
31       1.000000
32       0.500000
33       2.000000
34       2.000000
35       2.000000
36       2.000000
37       0.166667
38       0.166667
39       0.166667
40       0.166667
41       0.166667
42       0.166667
43       0.166667
44       0.166667
45       5.000000
46       5.000000
47       5.000000
48       5.000000
49       1.000000
50       0.500000
51       3.000000
52       0.416667
53       0.050000
54       0.050000
55       0

In [14]:
df['thin_film_thickness_nm'] = df['thin_film_thickness_nm'].fillna(df['thin_film_thickness_nm'].median())

In [15]:
df['stirring_time_hr'] = df['stirring_time_hr'].fillna(df['stirring_time_hr'].median())
df['stirring_temp_degC'] = df['stirring_temp_degC'].fillna(df['stirring_temp_degC'].median())

df['age_days'] = df['age_days'].fillna(0)
df['age_temp_degC'] = df['age_temp_degC'].fillna(0)

df['low_coating_time_sec'] = df['low_coating_time_sec'].fillna(0)
df['low_coating_rpm'] = df['low_coating_rpm'].fillna(0)

df['high_coating_time_sec'] = df['high_coating_time_sec'].fillna(df['high_coating_time_sec'].median())
df['high_coating_rpm'] = df['high_coating_rpm'].fillna(df['high_coating_rpm'].median())

df['dry_time_min'] = df['dry_time_min'].fillna(0)
df['dry_degC'] = df['dry_degC'].fillna(0)

df['pH'] = df['pH'].fillna(df['pH'].median())

df['bi_fe_ratio'] = df['bi_fe_ratio'].fillna(df['bi_fe_ratio'].median())

df['precursor_concentration'] = df['precursor_concentration'].fillna(df['precursor_concentration'].median())

In [16]:
codified_df = df.loc[:, column_filters['eda']]

codified_df.to_csv('./data/bfo_df_codified_20211123.csv', index=False)

display(codified_df)

recipe_id  nitrate_precs  bi_fe_ratio  separate_hydrolysis  \
0          1.0              1        1.100                    0   
1          2.0              1        1.050                    0   
2          3.0              1        1.100                    0   
3          4.0              1        1.100                    0   
4          5.0              1        1.100                    0   
5          6.0              1        1.100                    0   
6          7.0              1        1.100                    0   
7          8.0              1        1.050                    0   
8          9.0              1        1.100                    0   
9         10.0              1        1.100                    0   
10        11.0              1        1.100                    0   
11        12.0              1        1.100                    0   
12        13.0              1        1.050                    0   
13        14.0              1        1.100                    0   
14        15.0              1        1.100                    0   
15        16.0              1        1.000                    0   
16        17.0              1        1.050                    0   
17        18.0              1        1.100                    0   
18        19.0              1        1.150                    0   
19        20.0              1        1.300                    0   
20        21.0              1        1.050                    0   
21        22.0              1        1.050                    0   
22        23.0              1        1.000                    0   
23        24.0              1        1.050                    0   
24        25.0              1        1.050                    0   
25        26.0              1        1.050                    0   
26        27.0              1        1.050                    0   
27        28.0              1        1.050                    0   
28        29.0              1        1.050                    0   
29        30.0              1        1.100                    0   
30        31.0              1        1.100                    0   
31        32.0              1        1.050                    0   
32        33.0              1        1.090                    0   
33        34.0              1        1.000                    0   
34        35.0              1        1.000                    0   
35        36.0              1        1.000                    0   
36        37.0              1        1.000                    0   
37        38.0              1        1.000                    0   
38        39.0              1        1.050                    0   
39        40.0              1        1.100                    0   
40        41.0              1        1.150                    0   
41        42.0              1        1.000                    0   
42        43.0              1        1.050                    0   
43        44.0              1        1.100                    0   
44        45.0              1        1.150                    0   
45        46.0              1        1.000                    0   
46        47.0              1        1.050                    0   
47        48.0              1        1.100                    0   
48        49.0              1        1.150                    0   
49        50.0              1        1.050                    0   
50        51.0              1        1.100                    0   
51        52.0              1        1.050                    0   
52        53.0              1        1.100                    0   
53        54.0              1        1.000                    0   
54        55.0              1        1.000                    0   
55        56.0              1        1.000                    0   
56        57.0              1        1.000                    0   
57        58.0             -1        1.100                    0   
58        59.0              1        1.050          